Importar librerias

In [1]:
import pandas as pd
import requests
from datetime import datetime
import re

Importar los nuevos datos

In [2]:
# URL de la API con el token
api_url = "https://api.apify.com/v2/actor-tasks/frombini~google-maps-scraper-task/runs/last/dataset/items?token=apify_api_ZE7FMykxbpsHef9FAMxUqF9esYgIGK2LrElm&unwind=reviews&fields=placeId,reviews&omit=textTranslated,publishAt,likesCount,reviewId,reviewUrl,reviewerUrl,reviewerPhotoUrl,reviewerNumberOfReviews,isLocalGuide,rating,reviewImageUrls,reviewContext,reviewDetailedRating,name,responseFromOwnerDate,responseFromOwnerText"

# Realiza la solicitud GET
response = requests.get(api_url)

# Verifica el estado de la respuesta
if response.status_code == 200:
    # Parsea la respuesta JSON
    data = response.json()

    # Imprime los datos (o haz lo que desees con ellos)
    print(data)
else:
    print(f"Error en la solicitud: {response.status_code}, {response.text}")

nuevos_datosG = pd.DataFrame(data=data)
nuevos_datosG.head()

[{'placeId': 'ChIJF7Cnq1UDw4kRQu56t28mNTc', 'text': 'Horrible customer service from sales rep "Madison". Confused how people with horrible attitudes have a job. They don\'t do online returns without card despite having the receipt. Crazy lol', 'publishedAtDate': '2024-01-06T20:11:40.939Z', 'reviewerId': '100229735653203961126', 'stars': 1}, {'placeId': 'ChIJF7Cnq1UDw4kRQu56t28mNTc', 'text': None, 'publishedAtDate': '2023-08-24T23:06:32.181Z', 'reviewerId': '100332968402802728159', 'stars': 1}, {'placeId': 'ChIJF7Cnq1UDw4kRQu56t28mNTc', 'text': None, 'publishedAtDate': '2023-08-17T00:39:02.747Z', 'reviewerId': '102843264877927830425', 'stars': 5}, {'placeId': 'ChIJF7Cnq1UDw4kRQu56t28mNTc', 'text': None, 'publishedAtDate': '2023-06-15T11:41:30.310Z', 'reviewerId': '115056034124371774793', 'stars': 5}, {'placeId': 'ChIJF7Cnq1UDw4kRQu56t28mNTc', 'text': 'Bri helped me today. She was so knowledgeable and understanding. I am so impressed with her abilities and product knowledge. It’s been a 

placeId  \
0  ChIJF7Cnq1UDw4kRQu56t28mNTc   
1  ChIJF7Cnq1UDw4kRQu56t28mNTc   
2  ChIJF7Cnq1UDw4kRQu56t28mNTc   
3  ChIJF7Cnq1UDw4kRQu56t28mNTc   
4  ChIJF7Cnq1UDw4kRQu56t28mNTc   

                                                text  \
0  Horrible customer service from sales rep "Madi...   
1                                               None   
2                                               None   
3                                               None   
4  Bri helped me today. She was so knowledgeable ...   

            publishedAtDate             reviewerId  stars  
0  2024-01-06T20:11:40.939Z  100229735653203961126      1  
1  2023-08-24T23:06:32.181Z  100332968402802728159      1  
2  2023-08-17T00:39:02.747Z  102843264877927830425      5  
3  2023-06-15T11:41:30.310Z  115056034124371774793      5  
4  2023-06-02T21:13:09.772Z  103415787746138297190      5

Borramos las filas donde el texto sea nulo

In [3]:
nuevos_datosG.dropna(subset=['text'],inplace=True)

Borramos los duplicados

In [4]:
nuevos_datosG.drop_duplicates(inplace=True)

Renombramos los nombres de las columnas

In [5]:
nuevos_datosG = nuevos_datosG.rename(columns={'reviewerId': 'user_id','placeId':'place_id'})

Sacamos el mes , el año y la hora de la columna publishedAtDate

In [6]:
# Convertir la columna publishedAtDate a tipo datetime
nuevos_datosG['publishedAtDate'] = pd.to_datetime(nuevos_datosG['publishedAtDate'])

# Extraer el mes, el año y la hora
nuevos_datosG['month'] = nuevos_datosG['publishedAtDate'].dt.month
nuevos_datosG['year'] = nuevos_datosG['publishedAtDate'].dt.year
nuevos_datosG['hour'] = nuevos_datosG['publishedAtDate'].dt.hour

nuevos_datosG.drop(columns=['publishedAtDate'],inplace=True)

Reordenamos  las columnas

In [7]:
column_order = ['user_id', 'place_id', 'stars', 'text', 'month', 'year', 'hour']
nuevos_datosG = nuevos_datosG[column_order]

La columna texto se convierte a minusculas y quitamos los caracteres especiales

In [8]:
# We convert the text column to lowercase and remove the special characters

def limpiar_texto(texto):
    # Check if the value is a string
    if isinstance(texto, str):
        # Convert to lowercase
        texto = texto.lower()
        # Remove special characters using regular expressions
        texto = re.sub(r'[^a-z0-9\s]', '', texto)
    return texto

nuevos_datosG['text'] = nuevos_datosG['text'].apply(limpiar_texto)

In [9]:
nuevos_datosG

user_id                     place_id  stars  \
0      100229735653203961126  ChIJF7Cnq1UDw4kRQu56t28mNTc      1   
4      103415787746138297190  ChIJF7Cnq1UDw4kRQu56t28mNTc      5   
5      116853102905621355171  ChIJF7Cnq1UDw4kRQu56t28mNTc      1   
6      106546514463809678628  ChIJF7Cnq1UDw4kRQu56t28mNTc      1   
7      101669440777088764120  ChIJF7Cnq1UDw4kRQu56t28mNTc      2   
...                      ...                          ...    ...   
20262  113961751991816320565  ChIJn28ozfVZwokRHb8HiscE89c      5   
20264  116707014996352170051  ChIJn28ozfVZwokRHb8HiscE89c      5   
20265  114869326529043946124  ChIJn28ozfVZwokRHb8HiscE89c      5   
20267  110448191733650363365  ChIJn28ozfVZwokRHb8HiscE89c      5   
20268  115632472082895651773  ChIJn28ozfVZwokRHb8HiscE89c      1   

                                                    text  month  year  hour  
0      horrible customer service from sales rep madis...      1  2024    20  
4      bri helped me today she was so knowledgeable a...      6  2023    21  
5      today is my birthday i picked up a complimenta...      5  2023    21  
6      everytime i come here things be on sale i get ...      4  2023    23  
7      id like to start this off by saying krystal is...      1  2023     3  
...                                                  ...    ...   ...   ...  
20262  im super excited i am love so much my new hair...      4  2021     2  
20264  got my hair done by tre it is the best cut tre...      4  2021    20  
20265  workers were very willing to help and the plac...      4  2021     1  
20267  brand new clean products are easy to find cust...      3  2021    16  
20268  rather than assisting me or asking if i needed...      3  2021    20  

[12680 rows x 7 columns]

Tenemos que cambiar el place_id por el business_id

In [10]:
#Leemos la tabla de businessId_placeID
businessId_gmapID=pd.read_csv(r"D:\Datasets_proyecto\businessId_gmapID.csv")

In [11]:
# Reemplazar 'Sin Valores' en 'place_id' con el valor de 'business_id'
businessId_gmapID['place_id'] = businessId_gmapID.apply(lambda row: row['business_id'] if row['place_id'] == 'Sin Valores' else row['place_id'], axis=1)

# Concatenar por la columna 'place_id'
nuevos_datosG = pd.merge(businessId_gmapID, nuevos_datosG, on='place_id', how='inner')

#Borramos la columna place_id
nuevos_datosG.drop(columns=['Unnamed: 0','place_id'],inplace=True)


In [12]:
nuevos_datosG

business_id                user_id  stars  \
0      0x80e849691015d7b7:0x314b8627656bc6d5  115329747460485037083      5   
1      0x80e849691015d7b7:0x314b8627656bc6d5  117969807699447599252      1   
2      0x80e849691015d7b7:0x314b8627656bc6d5  116240990312661782957      4   
3      0x80e849691015d7b7:0x314b8627656bc6d5  107584768602612389480      5   
4      0x80e849691015d7b7:0x314b8627656bc6d5  107032221884595641777      5   
...                                      ...                    ...    ...   
12718  0x89acf761a874832d:0x111803f8757a81e0  117563084796957374772      5   
12719  0x89acf761a874832d:0x111803f8757a81e0  108580367348342416966      1   
12720  0x89acf761a874832d:0x111803f8757a81e0  106227575787840539569      5   
12721  0x89acf761a874832d:0x111803f8757a81e0  108375095338177593896      5   
12722  0x89acf761a874832d:0x111803f8757a81e0  101635235672012714005      5   

                                                    text  month  year  hour  
0      omar was amazing he was very helpful today dur...     12  2023    21  
1      i had intended to write a review but during my...     10  2023     6  
2      cosmetics and beauty products store  a wide ra...      8  2023    13  
3      love their customer service  they offer many s...      7  2023    14  
4      i love coming to this ulta the associate maddi...      6  2023    19  
...                                                  ...    ...   ...   ...  
12718                                   had my fav stuff      2  2021    23  
12719  i went to ulta because i was really excited to...      2  2021    19  
12720  because women like it when a man goes into a w...      1  2021    17  
12721                                         nice staff      1  2021     6  
12722  i went to see mandy for an eyebrow appointment...      1  2021     1  

[12723 rows x 7 columns]